<a href="https://colab.research.google.com/github/PrakritiShetty/GSoC2024-Overhaul_of_AuToBI/blob/main/DataPreprocessing_MakeTabular.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

The idea is to bring all the requisite datafiles to a tabular format. 2 columns for intermediate and intonational phrase boundaries, and 2 sub-columns for start and end timestamps

(Will later make it into textgrid and then ELAN)

Right now only phrase boundaries, later pitch accents and anything else is a plus.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


# NXT DATASET

In [ ]:
import glob
import numpy as np
import pandas as pd

In [ ]:
arr=[]

In [ ]:
directory = '/content/drive/MyDrive/NXT_FINAL'
for filename in glob.glob(directory+ '/*' ):
  with open(filename) as f:
    lines = f.readlines()
    for line in lines:
      if line.startswith("<break"):
        index = lines.index(line)
        nextline = lines[index+1]
        linesubs = line.split(' ')
        nextlinesubs = nextline.split(' ')
        id = linesubs[1].split("=")[1].split("\"")[1].split("\"")[0]
        href = nextlinesubs[1].split("=")[1].split("\"")[1].split("\"")[0]
        start = linesubs[2].split("=")[1].split("\"")[1].split("\"")[0]
        end = linesubs[3].split("=")[1].split("\"")[1].split("\"")[0]
        index = (linesubs[5].split("=")[1].split(">")[0]).split("\"")[1].split("\"")[0]
        if index=='3' or index=='4':
          entry = [id, href, start,end,index]
          arr.append(entry)

In [ ]:
df = pd.DataFrame(arr, columns = ['id','href','start','end','index'])
df.head()

id                                  href      start  \
0   sw2370A.break.5   sw2370.A.phonwords.xml#id(ms2A_pw4)   7.927250   
1  sw2370A.break.13  sw2370.A.phonwords.xml#id(ms2A_pw12)   9.632375   
2  sw2370A.break.27  sw2370.A.phonwords.xml#id(ms2A_pw26)  12.974000   
3  sw2370A.break.36  sw2370.A.phonwords.xml#id(ms2A_pw35)  15.574125   
4  sw2370A.break.40  sw2370.A.phonwords.xml#id(ms2A_pw39)  17.565500   

         end index  
0   7.927250     4  
1   9.632375     4  
2  12.974000     4  
3  15.574125     4  
4  17.565500     4

In [ ]:
df.to_excel( 'NXT_output.xlsx')

# BURSC

Prior preprocessing required: Copy all break files from within the nested directory structure and into 1 main folder (BURSC_FINAL)

In [ ]:
arr=[]

Extract requisite information from the break files

In [1]:
#directory that hold all the break files
directory = '/content/drive/MyDrive/BURSC_FINAL'


for filename in glob.glob(directory+ '/*' ):
  # print()
  with open(filename) as f:
    lines = f.readlines()
    id = filename.split('/')[-1]   # identifier for corresponding speech files
    # print(id)
    # color = lines[2].split(' ')[1]

    for idx, line in enumerate(lines):
      if line.startswith(" "): #This eliminates all the header lines from consideration.
        line = line.strip()
        line = line.split(' ')
        timestamp = line[0] #timestamp of occurence of the phrase boundary
        line = line[1:]

        for idx,string in enumerate(line):
          # Issues here are that the no of spaces at the beginning is not fixed (it can be 2 or 3)
          # The break index is also not the last element of the array, because occasionally 5/6 are also specified.
          if(string!=''):
            # print(idx)
            # print(line[idx:])
            line = line[idx:]
            if(1<len(line)):
              index = line[1]
            else:
              index = 0
            break

        #Handling for 3- and 4-
        if(index=='3-'):
          # print("inside")
          index = '3'
        if(index=='4-'):
          index = '4'

        # entry =
        # print(entry)

        # if(index=='3-'):
        #   print("still there")

        if(index=='3' or index=='4'):
          arr.append( [id, timestamp,index])
        else:
          arr.append( [id, timestamp,'0'])




# print(arr)




NameError: name 'glob' is not defined

In [ ]:
print(arr[1])

['F1AJRLP2.BRK', '0.569560', '0']


Make a dataframe and print to excel

In [ ]:
# Make a dataframe

df = pd.DataFrame(arr, columns = ['id','timestamp','index'])

df

id  timestamp index
0      F1AJRLP2.BRK   0.191410     0
1      F1AJRLP2.BRK   0.569560     0
2      F1AJRLP2.BRK   0.919700     0
3      F1AJRLP2.BRK   1.290000     4
4      F1AJRLP2.BRK   1.900091     0
...             ...        ...   ...
32239  M3BTRLP7.BRK  14.430451     0
32240  M3BTRLP7.BRK  15.265187     4
32241  M3BTRLP7.BRK  15.549699     0
32242  M3BTRLP7.BRK  15.837356     0
32243  M3BTRLP7.BRK  16.345146     4

[32244 rows x 3 columns]

In [2]:
# Write to excel

df.to_excel( 'bursc_output.xlsx')

Prior preprocessing required: Copy all speech files from the nested directory structure to one main folder (BURSC_AUDIO_FINAL)

In [3]:
# Convert all SPH files to wav files

import soundfile as sf
import os

input_folder = "/content/drive/MyDrive/BURSC_AUDIO_FINAL/"
output_folder = "/content/drive/MyDrive/wav_BURSC_AUDIO_FINAL"

# Create the output folder if it doesn't exist
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

# Iterate through .sph and .spn files and convert them to .wav
for file_name in os.listdir(input_folder):
    if file_name.endswith((".SPH", ".SPN")):
        input_path = os.path.join(input_folder, file_name)
        output_path = os.path.join(output_folder, file_name.replace(".SPH", ".wav").replace(".SPN", ".wav"))
        data, samplerate = sf.read(input_path)
        sf.write(output_path, data, samplerate)

KeyboardInterrupt: 

Extract all the frames from the audio files

In [ ]:
from transformers import AutoFeatureExtractor, WavLMForAudioFrameClassification
import torchaudio
import torch

feature_extractor = AutoFeatureExtractor.from_pretrained("patrickvonplaten/wavlm-libri-clean-100h-base-plus", padding=True)
model = WavLMForAudioFrameClassification.from_pretrained("patrickvonplaten/wavlm-libri-clean-100h-base-plus", output_hidden_states=True )


audio_folder = "/content/drive/MyDrive/wav_BURSC_AUDIO_FINAL"
all_files = os.listdir(audio_folder)

frame_size = int(0.5*feature_extractor.sampling_rate) # 50ms frame size
step_size =int( 0.01*feature_extractor.sampling_rate) #1ms step size
print(frame_size)
print(step_size)


frames=[]
k=-1;

#Construct the file paths
for index, audio_file in enumerate(all_files):
  path_to_audio_file = os.path.join(audio_folder, audio_file)
  audio_input, sample_rate = torchaudio.load(path_to_audio_file)
  # print(audio_input)


  for i in range(step_size, len(audio_input[0]), frame_size+step_size):
    k+=1
    # print("I",i)
    start_time = i/sample_rate
    end_time = (i+frame_size)/sample_rate

    min_frame_size = 16000
    frame = audio_input[: , max(0,i - step_size) : i + max(frame_size, min_frame_size) - step_size] # channels, time
    if frame.shape[1] < min_frame_size: #to handle end of audio files cases
      print(f"Skipping frame {k} due to insufficient size: {frame.shape[1]}")
      continue

    print("FRAME",frame)
    #process the frame using the feature extractor
    inputs = feature_extractor(frame.squeeze().numpy(), sampling_rate=sample_rate, return_tensors="pt")
    # print("INPUTS", inputs.input_values)

    with torch.no_grad():
      # use the model to generate embeddings for the frames
      embeddings = model(inputs.input_values).hidden_states[-1]
      # .last_hidden_state

    full_frame = {
        "ID":k,
        "name": audio_file,
        "start_time": start_time,
        "end_time": end_time,
        "embeddings": embeddings[0].numpy()
    }


    # print("FULL_FRAME",full_frame)


    frames.append(full_frame)

    remaining_files = len(all_files) - index
    print(f"Processed frame for audio '{audio_file}':")
    print(f"ID: {k}")
    print(f"  Start time: {start_time:.2f} seconds")
    print(f"  End time: {end_time:.2f} seconds")
    print(f"  Embeddings shape: {embeddings[0].shape}")
    print(f"Remaining files: {remaining_files}")
    print("=" * 40)


np.savez("all_frame_snippets.npz", frame_snippets=frames)

print("All frame snippets saved step by step to all_frame_snippets.npz")
print(f"Total number of frame snippets: {len(frames)}")





/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


preprocessor_config.json:   0%|          | 0.00/215 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/2.27k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/378M [00:00<?, ?B/s]

Some weights of WavLMForAudioFrameClassification were not initialized from the model checkpoint at patrickvonplaten/wavlm-libri-clean-100h-base-plus and are newly initialized: ['classifier.bias', 'classifier.weight', 'wavlm.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wavlm.encoder.pos_conv_embed.conv.parametrizations.weight.original1']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Streaming output truncated to the last 5000 lines.
ID: 2188
  Start time: 5.62 seconds
  End time: 6.12 seconds
  Embeddings shape: torch.Size([49, 768])
Remaining files: 22
FRAME tensor([[-0.0424, -0.0554, -0.0534,  ...,  0.0394,  0.0434,  0.0510]])
Processed frame for audio 'F1AS06P9.wav':
ID: 2189
  Start time: 6.13 seconds
  End time: 6.63 seconds
  Embeddings shape: torch.Size([49, 768])
Remaining files: 22
FRAME tensor([[0.1078, 0.1073, 0.1000,  ..., 0.0369, 0.0313, 0.0383]])
Processed frame for audio 'F1AS06P9.wav':
ID: 2190
  Start time: 6.64 seconds
  End time: 7.14 seconds
  Embeddings shape: torch.Size([49, 768])
Remaining files: 22
FRAME tensor([[ 0.0016,  0.0025,  0.0010,  ...,  0.0270,  0.0083, -0.0106]])
Processed frame for audio 'F1AS06P9.wav':
ID: 2191
  Start time: 7.15 seconds
  End time: 7.65 seconds
  Embeddings shape: torch.Size([49, 768])
Remaining files: 22
FRAME tensor([[-0.0446, -0.0457, -0.0436,  ...,  0.0188, -0.0043, -0.0072]])
Processed frame for audio 'F1

Final two dataframes -

*   df captures information from the break files
*   data captures information from the speech files



In [ ]:
data = pd.DataFrame(frames)

In [ ]:
data

ID          name  start_time  end_time  \
0        0  F1AJRLP1.wav        0.01      0.51   
1        1  F1AJRLP1.wav        0.52      1.02   
2        2  F1AJRLP1.wav        1.03      1.53   
3        3  F1AJRLP1.wav        1.54      2.04   
4        4  F1AJRLP1.wav        2.05      2.55   
...    ...           ...         ...       ...   
2704  2841  F1AS10P1.wav       20.41     20.91   
2705  2842  F1AS10P1.wav       20.92     21.42   
2706  2843  F1AS10P1.wav       21.43     21.93   
2707  2844  F1AS10P1.wav       21.94     22.44   
2708  2845  F1AS10P1.wav       22.45     22.95   

                                             embeddings  
0     [[0.2564065, -0.25831452, 0.20415506, 0.345056...  
1     [[0.180738, -0.2274944, 0.027218007, 0.2050423...  
2     [[0.13854294, -0.14366667, 0.05786131, 0.33907...  
3     [[0.0799949, -0.34184217, -0.013452978, -0.015...  
4     [[0.203503, -0.33939958, 0.23958156, 0.7843642...  
...                                                 ...  
2704  [[0.03232703, -0.32012728, 0.10847914, 0.72105...  
2705  [[0.14470297, -0.09415251, -0.1342027, 0.53942...  
2706  [[0.3428769, 0.00882759, -0.06580081, 0.357109...  
2707  [[0.27343407, -0.16050161, -0.05044606, 0.5344...  
2708  [[0.08519514, -0.029354705, -0.111788265, 0.22...  

[2709 rows x 5 columns]

In [ ]:
df

id  timestamp index
0      F1AJRLP2.BRK   0.191410     0
1      F1AJRLP2.BRK   0.569560     0
2      F1AJRLP2.BRK   0.919700     0
3      F1AJRLP2.BRK   1.290000     4
4      F1AJRLP2.BRK   1.900091     0
...             ...        ...   ...
32239  M3BTRLP7.BRK  14.430451     0
32240  M3BTRLP7.BRK  15.265187     4
32241  M3BTRLP7.BRK  15.549699     0
32242  M3BTRLP7.BRK  15.837356     0
32243  M3BTRLP7.BRK  16.345146     4

[32244 rows x 3 columns]

In [ ]:
for name in data['name']:
  name = name.split(".wav")[0]
data

ID          name  start_time  end_time  \
0        0  F1AJRLP1.wav        0.01      0.51   
1        1  F1AJRLP1.wav        0.52      1.02   
2        2  F1AJRLP1.wav        1.03      1.53   
3        3  F1AJRLP1.wav        1.54      2.04   
4        4  F1AJRLP1.wav        2.05      2.55   
...    ...           ...         ...       ...   
2704  2841  F1AS10P1.wav       20.41     20.91   
2705  2842  F1AS10P1.wav       20.92     21.42   
2706  2843  F1AS10P1.wav       21.43     21.93   
2707  2844  F1AS10P1.wav       21.94     22.44   
2708  2845  F1AS10P1.wav       22.45     22.95   

                                             embeddings  
0     [[0.2564065, -0.25831452, 0.20415506, 0.345056...  
1     [[0.180738, -0.2274944, 0.027218007, 0.2050423...  
2     [[0.13854294, -0.14366667, 0.05786131, 0.33907...  
3     [[0.0799949, -0.34184217, -0.013452978, -0.015...  
4     [[0.203503, -0.33939958, 0.23958156, 0.7843642...  
...                                                 ...  
2704  [[0.03232703, -0.32012728, 0.10847914, 0.72105...  
2705  [[0.14470297, -0.09415251, -0.1342027, 0.53942...  
2706  [[0.3428769, 0.00882759, -0.06580081, 0.357109...  
2707  [[0.27343407, -0.16050161, -0.05044606, 0.5344...  
2708  [[0.08519514, -0.029354705, -0.111788265, 0.22...  

[2709 rows x 5 columns]

Prepare to make a target break index column in the speech dataframe (data)

In [ ]:
convert_dict = {'timestamp': float}

df = df.astype(convert_dict)

In [ ]:
unique_names = data['name'].unique()
unique_names2 = df['id'].unique()

print((unique_names))
print((unique_names2))

['F1AJRLP1.wav' 'F1AJRLP2.wav' 'F1AJRLP4.wav' 'F1AJRLP3.wav'
 'F1AJRLP5.wav' 'F1APRLP2.wav' 'F1AJRLP6.wav' 'F1APRLP3.wav'
 'F1ARRLP1.wav' 'F1APRLP4.wav' 'F1ARRLP2.wav' 'F1ARRLP3.wav'
 'F1ARRLP4.wav' 'F1ARRLP6.wav' 'F1ARRLP5.wav' 'F1ARRLP7.wav'
 'F1ATRLP2.wav' 'F1AS02P1.wav' 'F1ATRLP4.wav' 'F1ATRLP3.wav'
 'F1ATRLP5.wav' 'F1ATRLP7.wav' 'F1ATRLP6.wav' 'F1AS02P3.wav'
 'F1AS02P2.wav' 'F1AS03P1.wav' 'F1AS03P2.wav' 'F1AS03P3.wav'
 'F1AS03P4.wav' 'F1AS03P5.wav' 'F1AS04P1.wav' 'F1AS04P2.wav'
 'F1AS04P5.wav' 'F1AS04P3.wav' 'F1AS04P4.wav' 'F1AS04P6.wav'
 'F1AS05P1.wav' 'F1AS04P7.wav' 'F1AS05P3.wav' 'F1AS05P2.wav'
 'F1AS05P5.wav' 'F1AS05P4.wav' 'F1AS06P1.wav' 'F1AS06P3.wav'
 'F1AS06P2.wav' 'F1AS06P5.wav' 'F1AS06P4.wav' 'F1AS06P7.wav'
 'F1AS06P6.wav' 'F1AS06P8.wav' 'F1AS06P9.wav' 'F1AS07P2.wav'
 'F1AS07P1.wav' 'F1AS07P5.wav' 'F1AS07P3.wav' 'F1AS07P4.wav'
 'F1AS08P2.wav' 'F1AS08P1.wav' 'F1AS08P4.wav' 'F1AS08P3.wav'
 'F1AS08P5.wav' 'F1AS08P6.wav' 'F1AS08P8.wav' 'F1AS08P7.wav'
 'F1AS09P1.wav' 'F1AS09P

In [ ]:
print(data.to_string())

In [ ]:
data

ID          name  start_time  end_time  \
0        0  F1AJRLP1.wav        0.01      0.51   
1        1  F1AJRLP1.wav        0.52      1.02   
2        2  F1AJRLP1.wav        1.03      1.53   
3        3  F1AJRLP1.wav        1.54      2.04   
4        4  F1AJRLP1.wav        2.05      2.55   
5        5  F1AJRLP1.wav        2.56      3.06   
6        6  F1AJRLP1.wav        3.07      3.57   
7        7  F1AJRLP1.wav        3.58      4.08   
8        8  F1AJRLP1.wav        4.09      4.59   
9        9  F1AJRLP1.wav        4.60      5.10   
10      10  F1AJRLP1.wav        5.11      5.61   
11      11  F1AJRLP1.wav        5.62      6.12   
12      12  F1AJRLP1.wav        6.13      6.63   
13      13  F1AJRLP1.wav        6.64      7.14   
14      14  F1AJRLP1.wav        7.15      7.65   
15      15  F1AJRLP1.wav        7.66      8.16   
16      16  F1AJRLP1.wav        8.17      8.67   
17      17  F1AJRLP1.wav        8.68      9.18   
18      18  F1AJRLP1.wav        9.19      9.69   
19      19  F1AJRLP1.wav        9.70     10.20   
20      20  F1AJRLP1.wav       10.21     10.71   
21      21  F1AJRLP1.wav       10.72     11.22   
22      22  F1AJRLP1.wav       11.23     11.73   
23      23  F1AJRLP1.wav       11.74     12.24   
24      24  F1AJRLP1.wav       12.25     12.75   
25      25  F1AJRLP1.wav       12.76     13.26   
26      26  F1AJRLP1.wav       13.27     13.77   
27      27  F1AJRLP1.wav       13.78     14.28   
28      28  F1AJRLP1.wav       14.29     14.79   
29      29  F1AJRLP1.wav       14.80     15.30   
30      30  F1AJRLP1.wav       15.31     15.81   
31      31  F1AJRLP1.wav       15.82     16.32   
32      32  F1AJRLP1.wav       16.33     16.83   
33      33  F1AJRLP1.wav       16.84     17.34   
34      34  F1AJRLP1.wav       17.35     17.85   
35      35  F1AJRLP1.wav       17.86     18.36   
36      36  F1AJRLP1.wav       18.37     18.87   
37      37  F1AJRLP1.wav       18.88     19.38   
38      38  F1AJRLP1.wav       19.39     19.89   
39      39  F1AJRLP1.wav       19.90     20.40   
40      40  F1AJRLP1.wav       20.41     20.91   
41      41  F1AJRLP1.wav       20.92     21.42   
42      42  F1AJRLP1.wav       21.43     21.93   
43      43  F1AJRLP1.wav       21.94     22.44   
44      44  F1AJRLP1.wav       22.45     22.95   
45      45  F1AJRLP1.wav       22.96     23.46   
46      46  F1AJRLP1.wav       23.47     23.97   
47      47  F1AJRLP1.wav       23.98     24.48   
48      50  F1AJRLP2.wav        0.01      0.51   
49      51  F1AJRLP2.wav        0.52      1.02   
50      52  F1AJRLP2.wav        1.03      1.53   
51      53  F1AJRLP2.wav        1.54      2.04   
52      54  F1AJRLP2.wav        2.05      2.55   
53      55  F1AJRLP2.wav        2.56      3.06   
54      56  F1AJRLP2.wav        3.07      3.57   
55      57  F1AJRLP2.wav        3.58      4.08   
56      58  F1AJRLP2.wav        4.09      4.59   
57      59  F1AJRLP2.wav        4.60      5.10   
58      60  F1AJRLP2.wav        5.11      5.61   
59      61  F1AJRLP2.wav        5.62      6.12   
60      62  F1AJRLP2.wav        6.13      6.63   
61      63  F1AJRLP2.wav        6.64      7.14   
62      64  F1AJRLP2.wav        7.15      7.65   
63      65  F1AJRLP2.wav        7.66      8.16   
64      66  F1AJRLP2.wav        8.17      8.67   
65      67  F1AJRLP2.wav        8.68      9.18   
66      68  F1AJRLP2.wav        9.19      9.69   
67      69  F1AJRLP2.wav        9.70     10.20   
68      70  F1AJRLP2.wav       10.21     10.71   
69      71  F1AJRLP2.wav       10.72     11.22   
70      72  F1AJRLP2.wav       11.23     11.73   
71      73  F1AJRLP2.wav       11.74     12.24   
72      74  F1AJRLP2.wav       12.25     12.75   
73      75  F1AJRLP2.wav       12.76     13.26   
74      76  F1AJRLP2.wav       13.27     13.77   
75      77  F1AJRLP2.wav       13.78     14.28   
76      78  F1AJRLP2.wav       14.29     14.79   
77      79  F1AJRLP2.wav       14.80     15.30   
78      80  F1AJRLP2.wav       15.31     15.81   
79      

In [ ]:
pd.set_option('display.max_rows', None)
print(data)

        ID          name  start_time  end_time  \
0        0  F1AJRLP1.wav        0.01      0.51   
1        1  F1AJRLP1.wav        0.52      1.02   
2        2  F1AJRLP1.wav        1.03      1.53   
3        3  F1AJRLP1.wav        1.54      2.04   
4        4  F1AJRLP1.wav        2.05      2.55   
5        5  F1AJRLP1.wav        2.56      3.06   
6        6  F1AJRLP1.wav        3.07      3.57   
7        7  F1AJRLP1.wav        3.58      4.08   
8        8  F1AJRLP1.wav        4.09      4.59   
9        9  F1AJRLP1.wav        4.60      5.10   
10      10  F1AJRLP1.wav        5.11      5.61   
11      11  F1AJRLP1.wav        5.62      6.12   
12      12  F1AJRLP1.wav        6.13      6.63   
13      13  F1AJRLP1.wav        6.64      7.14   
14      14  F1AJRLP1.wav        7.15      7.65   
15      15  F1AJRLP1.wav        7.66      8.16   
16      16  F1AJRLP1.wav        8.17      8.67   
17      17  F1AJRLP1.wav        8.68      9.18   
18      18  F1AJRLP1.wav        9.19      9.69   


In [ ]:
data[data['name'] == 'F1AJRLP1.wav']

ID          name  start_time  end_time  \
0    0  F1AJRLP1.wav        0.01      0.51   
1    1  F1AJRLP1.wav        0.52      1.02   
2    2  F1AJRLP1.wav        1.03      1.53   
3    3  F1AJRLP1.wav        1.54      2.04   
4    4  F1AJRLP1.wav        2.05      2.55   
5    5  F1AJRLP1.wav        2.56      3.06   
6    6  F1AJRLP1.wav        3.07      3.57   
7    7  F1AJRLP1.wav        3.58      4.08   
8    8  F1AJRLP1.wav        4.09      4.59   
9    9  F1AJRLP1.wav        4.60      5.10   
10  10  F1AJRLP1.wav        5.11      5.61   
11  11  F1AJRLP1.wav        5.62      6.12   
12  12  F1AJRLP1.wav        6.13      6.63   
13  13  F1AJRLP1.wav        6.64      7.14   
14  14  F1AJRLP1.wav        7.15      7.65   
15  15  F1AJRLP1.wav        7.66      8.16   
16  16  F1AJRLP1.wav        8.17      8.67   
17  17  F1AJRLP1.wav        8.68      9.18   
18  18  F1AJRLP1.wav        9.19      9.69   
19  19  F1AJRLP1.wav        9.70     10.20   
20  20  F1AJRLP1.wav       10.21     10.71   
21  21  F1AJRLP1.wav       10.72     11.22   
22  22  F1AJRLP1.wav       11.23     11.73   
23  23  F1AJRLP1.wav       11.74     12.24   
24  24  F1AJRLP1.wav       12.25     12.75   
25  25  F1AJRLP1.wav       12.76     13.26   
26  26  F1AJRLP1.wav       13.27     13.77   
27  27  F1AJRLP1.wav       13.78     14.28   
28  28  F1AJRLP1.wav       14.29     14.79   
29  29  F1AJRLP1.wav       14.80     15.30   
30  30  F1AJRLP1.wav       15.31     15.81   
31  31  F1AJRLP1.wav       15.82     16.32   
32  32  F1AJRLP1.wav       16.33     16.83   
33  33  F1AJRLP1.wav       16.84     17.34   
34  34  F1AJRLP1.wav       17.35     17.85   
35  35  F1AJRLP1.wav       17.86     18.36   
36  36  F1AJRLP1.wav       18.37     18.87   
37  37  F1AJRLP1.wav       18.88     19.38   
38  38  F1AJRLP1.wav       19.39     19.89   
39  39  F1AJRLP1.wav       19.90     20.40   
40  40  F1AJRLP1.wav       20.41     20.91   
41  41  F1AJRLP1.wav       20.92     21.42   
42  42  F1AJRLP1.wav       21.43     21.93   
43  43  F1AJRLP1.wav       21.94     22.44   
44  44  F1AJRLP1.wav       22.45     22.95   
45  45  F1AJRLP1.wav       22.96     23.46   
46  46  F1AJRLP1.wav       23.47     23.97   
47  47  F1AJRLP1.wav       23.98     24.48   

                                           embeddings  
0   [[0.2564065, -0.25831452, 0.20415506, 0.345056...  
1   [[0.180738, -0.2274944, 0.027218007, 0.2050423...  
2   [[0.13854294, -0.14366667, 0.05786131, 0.33907...  
3   [[0.0799949, -0.34184217, -0.013452978, -0.015...  
4   [[0.203503, -0.33939958, 0.23958156, 0.7843642...  
5   [[0.15819977, -0.056827664, 0.074282974, 0.392...  
6   [[0.23474598, -0.2936242, -0.041299764, 0.6581...  
7   [[0.21797721, -0.40040615, 0.23808244, 0.45597...  
8   [[0.3166269, -0.21566156, 0.071921356, 0.61812...  
9   [[0.30487707, -0.29699358, 0.04419234, 0.43886...  
10  [[0.10077356, 0.053034566, 0.0029149256, 0.475...  
11  [[0.09317018, 0.018412825, 0.0051124827, 0.483...  
12  [[0.34862772, -0.052189525, 0.08634903, 0.6538...  
13  [[0.24805291, -0.137552, 0.047147542, 0.759634...  
14  [[0.2641128, -0.09932413, 0.12730135, 0.627631...  
15  [[0.11095869, -0.30331522, 0.006540933, 0.0564...  
16  [[0.3234344, -0.09618746, -0.119927526, -0.026...  
17  [[0.1578516, -0.24914564, 0.0007767226, 0.5538...  
18  [[0.14663269, -0.35199296, 0.08122695, 0.69552...  
19  [[0.3338562, -0.23709643, -0.025959797, 0.3023...  
20  [[0.26132458, -0.056013305, -0.08802485, 0.710...  
21  [[0.4749416, -0.027936155, -0.09133479, 0.6015...  
22  [[0.080737814, -0.07208234, 0.043418717, 0.091...  
23  [[0.26073134, 0.03420421, 0.23022068, 0.625827...  
24  [[0.23479201, -0.34353647, 0.25310206, 0.50009...  
25  [[0.25342026, -0.1381653, 0.129562, 0.42276305...  
26  [[0.45413837, -0.122402385, -0.090201415, 0.19...  
27  [[0.045191683, 0.058557976, -0.02307039, 0.066...  
28  [[0.13014768, -0.14580002, -0.072266586, 0.379...  
29  [[0.31852236, -0.09336982, -0.10109205, 0.4781...  
30  [[0.16231

In [ ]:
df[df['id'] == 'F1ATRLP2.wav'.split('.wav')[0] +".BRK"]

id  timestamp index
1162  F1ATRLP2.BRK   0.900000     0
1163  F1ATRLP2.BRK   1.310000     0
1164  F1ATRLP2.BRK   1.770000     0
1165  F1ATRLP2.BRK   2.450000     4
1166  F1ATRLP2.BRK   2.890000     0
1167  F1ATRLP2.BRK   3.070000     0
1168  F1ATRLP2.BRK   3.150000     0
1169  F1ATRLP2.BRK   3.990000     3
1170  F1ATRLP2.BRK   4.690000     0
1171  F1ATRLP2.BRK   5.310000     0
1172  F1ATRLP2.BRK   5.760000     0
1173  F1ATRLP2.BRK   6.400000     4
1174  F1ATRLP2.BRK   6.560000     0
1175  F1ATRLP2.BRK   6.950000     0
1176  F1ATRLP2.BRK   7.390000     4
1177  F1ATRLP2.BRK   8.320000     0
1178  F1ATRLP2.BRK   8.380000     0
1179  F1ATRLP2.BRK   8.720000     4
1180  F1ATRLP2.BRK   8.930000     0
1181  F1ATRLP2.BRK   9.310000     0
1182  F1ATRLP2.BRK   9.780000     3
1183  F1ATRLP2.BRK   9.890000     0
1184  F1ATRLP2.BRK  10.140000     0
1185  F1ATRLP2.BRK  10.570000     0
1186  F1ATRLP2.BRK  11.120000     3
1187  F1ATRLP2.BRK  11.740000     0
1188  F1ATRLP2.BRK  12.070000     3
1189  F1ATRLP2.BRK  12.200000     0
1190  F1ATRLP2.BRK  12.670000     0
1191  F1ATRLP2.BRK  13.130000     4
1192  F1ATRLP2.BRK  13.640000     0
1193  F1ATRLP2.BRK  13.700000     0
1194  F1ATRLP2.BRK  14.270000     3
1195  F1ATRLP2.BRK  14.350000     0
1196  F1ATRLP2.BRK  14.920000     0
1197  F1ATRLP2.BRK  15.200000     0
1198  F1ATRLP2.BRK  15.560000     4
1199  F1ATRLP2.BRK  16.129999     0
1200  F1ATRLP2.BRK  16.209999     0
1201  F1ATRLP2.BRK  16.430000     0
1202  F1ATRLP2.BRK  16.969999     4
1203  F1ATRLP2.BRK  17.420000     0
1204  F1ATRLP2.BRK  17.549999     0
1205  F1ATRLP2.BRK  17.740000     0
1206  F1ATRLP2.BRK  17.879999     0
1207  F1ATRLP2.BRK  17.969999     0
1208  F1ATRLP2.BRK  18.410000     4

In [ ]:
x = data[data['name'] == 'F1AJRLP2.wav']
x
y = df[df['id'] == 'F1AJRLP2.wav'.split('.wav')[0] +".BRK"]
y

id  timestamp index
0   F1AJRLP2.BRK   0.191410     0
1   F1AJRLP2.BRK   0.569560     0
2   F1AJRLP2.BRK   0.919700     0
3   F1AJRLP2.BRK   1.290000     4
4   F1AJRLP2.BRK   1.900091     0
5   F1AJRLP2.BRK   2.150000     3
6   F1AJRLP2.BRK   2.441640     0
7   F1AJRLP2.BRK   3.081229     4
8   F1AJRLP2.BRK   3.562087     0
9   F1AJRLP2.BRK   3.590099     0
10  F1AJRLP2.BRK   4.229687     0
11  F1AJRLP2.BRK   4.710545     4
12  F1AJRLP2.BRK   4.829524     0
13  F1AJRLP2.BRK   5.870606     3
14  F1AJRLP2.BRK   6.351464     0
15  F1AJRLP2.BRK   6.869671     4
16  F1AJRLP2.BRK   7.419879     0
17  F1AJRLP2.BRK   7.690654     0
18  F1AJRLP2.BRK   8.360000     4
19  F1AJRLP2.BRK   8.839112     0
20  F1AJRLP2.BRK   9.389998     4
21  F1AJRLP2.BRK   9.539391     0
22  F1AJRLP2.BRK   9.800829     0
23  F1AJRLP2.BRK   9.870857     0
24  F1AJRLP2.BRK  10.141631     0
25  F1AJRLP2.BRK  10.491771     0
26  F1AJRLP2.BRK  10.930000     0
27  F1AJRLP2.BRK  11.310000     4
28  F1AJRLP2.BRK  12.030000     0
29  F1AJRLP2.BRK  12.640000     4
30  F1AJRLP2.BRK  12.690430     0
31  F1AJRLP2.BRK  12.870000     0
32  F1AJRLP2.BRK  13.210000     0
33  F1AJRLP2.BRK  13.560000     3
34  F1AJRLP2.BRK  13.829539     0
35  F1AJRLP2.BRK  13.869700     0
36  F1AJRLP2.BRK  14.510000     0
37  F1AJRLP2.BRK  14.970000     4
38  F1AJRLP2.BRK  15.300137     0
39  F1AJRLP2.BRK  15.740000     0
40  F1AJRLP2.BRK  15.840000     0
41  F1AJRLP2.BRK  15.890000     0
42  F1AJRLP2.BRK  16.360000     0
43  F1AJRLP2.BRK  16.610000     4
44  F1AJRLP2.BRK  17.081699     0
45  F1AJRLP2.BRK  17.249766     0
46  F1AJRLP2.BRK  17.350000     0
47  F1AJRLP2.BRK  17.430000     0
48  F1AJRLP2.BRK  17.910000     3
49  F1AJRLP2.BRK  18.160129     0
50  F1AJRLP2.BRK  18.790381     3
51  F1AJRLP2.BRK  19.180000     0
52  F1AJRLP2.BRK  19.420632     0
53  F1AJRLP2.BRK  19.892153     4
54  F1AJRLP2.BRK  20.001432     0
55  F1AJRLP2.BRK  20.370246     0
56  F1AJRLP2.BRK  20.720386     0
57  F1AJRLP2.BRK  21.149890     4
58  F1AJRLP2.BRK  21.890000     0
59  F1AJRLP2.BRK  22.160000     4
60  F1AJRLP2.BRK  22.680000     0
61  F1AJRLP2.BRK  23.140000     4
62  F1AJRLP2.BRK  23.341332     0
63  F1AJRLP2.BRK  23.880000     3
64  F1AJRLP2.BRK  23.980920     0
65  F1AJRLP2.BRK  24.041611     0
66  F1AJRLP2.BRK  24.670000     0
67  F1AJRLP2.BRK  24.930000     0
68  F1AJRLP2.BRK  25.670000     4
69  F1AJRLP2.BRK  26.021480     0
70  F1AJRLP2.BRK  26.530350     0
71  F1AJRLP2.BRK  26.759108     0
72  F1AJRLP2.BRK  27.230629     4

In [ ]:
# unique_names = data['name'].unique()
# unique_names2 = df['id'].unique()

# # print(len(unique_names))
# # print(len(unique_names2))

# # print(unique_names)
# # print(unique_names2)

# # unique_names

# for i in unique_names:
#     if i.split('.wav')[0] +".BRK" in unique_names2:

#     #  i = i.split('.wav')[0] + ".BRK"
#     #  print(i)
#       x = data[data['name'] == i]
#       y = df[df['id'] == i.split('.wav')[0] +".BRK"]

#       # print("len X", len(x))
#       # print("len Y", len(y))
#       # print("X", x)
#       # print("Y", y)


#       def new_col(row):
#         # k=0;
#         ans=[]
#         # print(y['timestamp'].iloc[k])
#         print(row)
#         print(row.start_time)
#         print(row.end_time)
#         # print(y["timestamp"])

#         for k in range (0,len(y["timestamp"])-1):
#           if y["timestamp"].iloc[k] > row.end_time:
#             break

#           while (y["timestamp"].iloc[k] >= row.start_time) & (y["timestamp"].iloc[k] <= row.end_time and k<len(y['timestamp'])):
#             ans.append(y["index"].iloc[k])
#             k+=1
#             print("ANS", ans)


#         if(len(ans)==0):
#            ans.append(0)
#         if(len(ans)>1):
#             if '3' in ans:
#               ans = ['3']
#             if '4' in ans:
#               ans = ['4']

#         print('ANS FINAL', ans)
#         return ans
#         # print(y[condition])
#         # return y[condition]["index"]

#       data.apply(new_col, axis=1)
#       # data["target"] = data.apply(new_col, axis=1)
#       # print(data.apply(new_col, axis=1))
#       # # continue

# # print("len X", len(x))
# # print("len Y", len(y))

# # data

ID                                                            0
name                                               F1AJRLP1.wav
start_time                                                 0.01
end_time                                                   0.51
embeddings    [[0.2564065, -0.25831452, 0.20415506, 0.345056...
Name: 0, dtype: object
0.01
0.51
ANS FINAL [0]
ID                                                            1
name                                               F1AJRLP1.wav
start_time                                                 0.52
end_time                                                   1.02
embeddings    [[0.180738, -0.2274944, 0.027218007, 0.2050423...
Name: 1, dtype: object
0.52
1.02
ANS ['4']
ANS FINAL ['4']
ID                                                            2
name                                               F1AJRLP1.wav
start_time                                                 1.03
end_time                                                   1.5

KeyboardInterrupt: 

In [ ]:
def new_col(row):
  # x = data[data['name'] == ]
  # print(row['name'])
  i = row['name']
  # print(i)

  # data has 2709 rows, and df has 32,244. Hence choose only those break files which have a corresponding frame
  y = df[df['id'] == i.split('.wav')[0] +".BRK"]
  # k=0;
  ans=[]
  # print(y['timestamp'].iloc[k])
  print(row)
  print(row.start_time)
  print(row.end_time)
  # print(y["timestamp"
  for k in range (0,len(y["timestamp"])-1):
    if y["timestamp"].iloc[k] > row.end_time:
      break

    while (y["timestamp"].iloc[k] >= row.start_time) & (y["timestamp"].iloc[k] <= row.end_time and k<len(y['timestamp'])):
      ans.append(y["index"].iloc[k])
      k+=1
      print("ANS", ans)

  if(len(ans)==0):
     ans=['0']

  if(len(ans)>1):
      if '3' in ans:
        ans = ['3']
      if '4' in ans:
        ans = ['4']
      else:
        ans = ['0']

  finalans = ans[0]
  print('ANS FINAL', finalans)

  return finalans
  # print(y[condition])
  # return y[condition]["index


data['label'] = data.apply(new_col, axis=1)

Streaming output truncated to the last 5000 lines.
ANS ['4']
ANS ['4', '0']
ANS ['4', '0', '0']
ANS FINAL 4
ID                                                         2412
name                                               F1AS08P4.wav
start_time                                                14.29
end_time                                                  14.79
embeddings    [[0.113148905, -0.28869617, -0.004316934, 0.09...
label                                                       [3]
Name: 2301, dtype: object
14.29
14.79
ANS ['3']
ANS FINAL 3
ID                                                         2413
name                                               F1AS08P4.wav
start_time                                                 14.8
end_time                                                   15.3
embeddings    [[0.38969156, -0.11948719, 0.018548815, 0.6856...
label                                                       [4]
Name: 2302, dtype: object
14.8
15.3
ANS ['4']
ANS FINAL 4
ID    

In [ ]:
data

ID          name  start_time  end_time  \
0        0  F1AJRLP1.wav        0.01      0.51   
1        1  F1AJRLP1.wav        0.52      1.02   
2        2  F1AJRLP1.wav        1.03      1.53   
3        3  F1AJRLP1.wav        1.54      2.04   
4        4  F1AJRLP1.wav        2.05      2.55   
5        5  F1AJRLP1.wav        2.56      3.06   
6        6  F1AJRLP1.wav        3.07      3.57   
7        7  F1AJRLP1.wav        3.58      4.08   
8        8  F1AJRLP1.wav        4.09      4.59   
9        9  F1AJRLP1.wav        4.60      5.10   
10      10  F1AJRLP1.wav        5.11      5.61   
11      11  F1AJRLP1.wav        5.62      6.12   
12      12  F1AJRLP1.wav        6.13      6.63   
13      13  F1AJRLP1.wav        6.64      7.14   
14      14  F1AJRLP1.wav        7.15      7.65   
15      15  F1AJRLP1.wav        7.66      8.16   
16      16  F1AJRLP1.wav        8.17      8.67   
17      17  F1AJRLP1.wav        8.68      9.18   
18      18  F1AJRLP1.wav        9.19      9.69   
19      19  F1AJRLP1.wav        9.70     10.20   
20      20  F1AJRLP1.wav       10.21     10.71   
21      21  F1AJRLP1.wav       10.72     11.22   
22      22  F1AJRLP1.wav       11.23     11.73   
23      23  F1AJRLP1.wav       11.74     12.24   
24      24  F1AJRLP1.wav       12.25     12.75   
25      25  F1AJRLP1.wav       12.76     13.26   
26      26  F1AJRLP1.wav       13.27     13.77   
27      27  F1AJRLP1.wav       13.78     14.28   
28      28  F1AJRLP1.wav       14.29     14.79   
29      29  F1AJRLP1.wav       14.80     15.30   
30      30  F1AJRLP1.wav       15.31     15.81   
31      31  F1AJRLP1.wav       15.82     16.32   
32      32  F1AJRLP1.wav       16.33     16.83   
33      33  F1AJRLP1.wav       16.84     17.34   
34      34  F1AJRLP1.wav       17.35     17.85   
35      35  F1AJRLP1.wav       17.86     18.36   
36      36  F1AJRLP1.wav       18.37     18.87   
37      37  F1AJRLP1.wav       18.88     19.38   
38      38  F1AJRLP1.wav       19.39     19.89   
39      39  F1AJRLP1.wav       19.90     20.40   
40      40  F1AJRLP1.wav       20.41     20.91   
41      41  F1AJRLP1.wav       20.92     21.42   
42      42  F1AJRLP1.wav       21.43     21.93   
43      43  F1AJRLP1.wav       21.94     22.44   
44      44  F1AJRLP1.wav       22.45     22.95   
45      45  F1AJRLP1.wav       22.96     23.46   
46      46  F1AJRLP1.wav       23.47     23.97   
47      47  F1AJRLP1.wav       23.98     24.48   
48      50  F1AJRLP2.wav        0.01      0.51   
49      51  F1AJRLP2.wav        0.52      1.02   
50      52  F1AJRLP2.wav        1.03      1.53   
51      53  F1AJRLP2.wav        1.54      2.04   
52      54  F1AJRLP2.wav        2.05      2.55   
53      55  F1AJRLP2.wav        2.56      3.06   
54      56  F1AJRLP2.wav        3.07      3.57   
55      57  F1AJRLP2.wav        3.58      4.08   
56      58  F1AJRLP2.wav        4.09      4.59   
57      59  F1AJRLP2.wav        4.60      5.10   
58      60  F1AJRLP2.wav        5.11      5.61   
59      61  F1AJRLP2.wav        5.62      6.12   
60      62  F1AJRLP2.wav        6.13      6.63   
61      63  F1AJRLP2.wav        6.64      7.14   
62      64  F1AJRLP2.wav        7.15      7.65   
63      65  F1AJRLP2.wav        7.66      8.16   
64      66  F1AJRLP2.wav        8.17      8.67   
65      67  F1AJRLP2.wav        8.68      9.18   
66      68  F1AJRLP2.wav        9.19      9.69   
67      69  F1AJRLP2.wav        9.70     10.20   
68      70  F1AJRLP2.wav       10.21     10.71   
69      71  F1AJRLP2.wav       10.72     11.22   
70      72  F1AJRLP2.wav       11.23     11.73   
71      73  F1AJRLP2.wav       11.74     12.24   
72      74  F1AJRLP2.wav       12.25     12.75   
73      75  F1AJRLP2.wav       12.76     13.26   
74      76  F1AJRLP2.wav       13.27     13.77   
75      77  F1AJRLP2.wav       13.78     14.28   
76      78  F1AJRLP2.wav       14.29     14.79   
77      79  F1AJRLP2.wav       14.80     15.30   
78      80  F1AJRLP2.wav       15.31     15.81   
79      

In [ ]:
data.to_excel( 'final_bursc_data.xlsx')


In [ ]:
# k=0;

# for i in unique_names:
#     if i.split('.wav')[0] +".BRK" in unique_names2:
#       print(i)
#       k+=1

# print(k)

In [ ]:
# data

In [ ]:
# timestamps = df['timestamp']

# timestamps


In [ ]:
# for frame in frames:
#   # print(frame)
#   for time in timestamp:
#     print(time, frame)